# How many remain?

The question we try to answer here is: Suppose that on a given day we observe $k$ new infections, how many exposed (infected but not infectious) individuals remain in the population? We do this as follows, using "reasonable" values of the epidemic rate parameters and a physical distancing network model fitted to the observed time series data we simulate a large ($N=100$ - or maybe more, once I gt it working) number of dynamics and read-off the infected and exposed nubers in the tail of the transmission urve to get a conditional PDF - the final figure.

## Load in the data and define the various parameters:

Find the point of inflection (what is called turning point below) in the total nmber of infections

In [3]:
cd("/Users/michael/work/GitHub/epinets")
include("EpiSim.jl")
using CSV
using Plots
using LightGraphs
using JLD2, FileIO
cd("/Users/michael/work/GitHub/COVID-19/csse_covid_19_data/csse_covid_19_time_series")
file="time_series_covid19_confirmed_global.csv"
allstates=["Australian Capital Territory" "New South Wales"  "Northern Territory" "Queensland" "South Australia" "Tasmania" "Victoria" "Western Australia"]
allcities=["Canberra" "Sydney" "Darwin" "Brisbane" "Adelaide" "Hobart" "Melbourne" "Perth"]
z=[]
for state in allstates
    z=push!(z,EpiSim.getdata("Australia",state))
end
ddays=CSV.File(file)[1]
ddays=propertynames(ddays,4)[5:end]
ddays=String.(ddays)
ndays=length(ddays)
pops=[426709 8089526 245869 5095100 1751693 534281 6594804 2621680]
cpop=[447457 4741874 132708 2326656 1315346 208324 4677157 2004696]
#'reasonable' parameters
epiparam=Dict()
epiparam["p0"]=0.2 #a guess - tuned to match observed data 
epiparam["p2"]=1/12 #revised infection rate with distancing measure
epiparam["q"]=1/7 #"up to" two weeks
epiparam["r0"]=1/14 #about two weeks for mild, 3-6 for severe
epiparam["r2"]=1/4 #revised removal rate (now due to testing and isolation)
epiparam["nseeds"]=5 #probably too many, consider dropping.

5

## Simulate with isolation 

In [4]:
i=7 # Melbourne
epiparam["pop"]=pops[i]
epiparam["gridsize"]=Int(floor(sqrt(pops[i])))
y=z[i];
ddt(z,zt)=count(z->z>0, z[1:zt])+ count(z->z<0, z[zt+1:end])
~,tpday=findmax([ddt(diff(diff(y)),nx) for nx in 1:(ndays-2)])
#this is the turning point between exponential growth and decay. totItp total infections at day tpday
totItp=y[tpday+1]
plot(1:tpday+1,y[1:tpday+1],lw=4,label="growth phase",title=allstates[i])
plot!(tpday+1:ndays,y[tpday+1:ndays],lw=4,label="plateau")
cd("/Users/michael/work/GitHub/epinets")

In [5]:
gridsize=epiparam["gridsize"]
pop=epiparam["pop"]
bamodel=barabasi_albert(gridsize^2, 3, 2)
lattice=LightGraphs.grid((gridsize,gridsize),periodic=true)
wattstrog95=watts_strogatz(gridsize^2, 4, 0.013)  #s=0.013 => 95% compliance
wattstrog90=watts_strogatz(gridsize^2, 4, 0.026)  #s=0.026 => 90% compliance
wattstrog80=watts_strogatz(gridsize^2, 4, 0.053)  #s=0.053 => 80% compliance
St95,Et95,It95,Rt95=EpiSim.episim(bamodel,wattstrog95, epiparam, totItp, tpday+2, 90, 100)
St90,Et90,It90,Rt90=EpiSim.episim(bamodel,wattstrog90, epiparam, totItp, tpday+2, 90, 100)
St80,Et80,It80,Rt80=EpiSim.episim(bamodel,wattstrog80, epiparam, totItp, tpday+2, 90, 100)

100.0%┣████████████████████████████████████████┫ 100/100 [38:30<00:00, 0.0 it/s]
100.0%┣████████████████████████████████████████┫ 100/100 [44:31<00:00, 0.0 it/s]
100.0%┣████████████████████████████████████████┫ 100/100 [54:28<00:00, 0.0 it/s]


(UInt64[0x000000000064a0f4 0x000000000064a0f4 … 0x000000000064a0f4 0x000000000064a0f4; 0x000000000064a0f4 0x000000000064a0f4 … 0x000000000064a0f4 0x000000000064a0f4; … ; 0x0000000000648ce4 0x000000000064874c … 0x000000000064919e 0x000000000064929a; 0x0000000000648ce4 0x000000000064874c … 0x000000000064919b 0x0000000000649298], UInt64[0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; 0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; … ; 0x0000000000000027 0x0000000000000031 … 0x0000000000000017 0x0000000000000012; 0x000000000000001d 0x0000000000000029 … 0x0000000000000018 0x0000000000000012], UInt64[0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; 0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; … ; 0x0000000000000016 0x0000000000000022 … 0x0000000000000010 0x0000000000000008; 0x000000000000001d 0x0000000000000024 … 0x000000000000000b 0x0000000000000008], UInt64[0x000000

## And plot
... for Melbourne ...

In [6]:
plot(ddays,y,size=(1200,600),label=false)
EpiSim.plotquantiles(pop .- (Et90+St90),:blue,"90% Compliance")
EpiSim.plotquantiles(pop .- (Et95+St95),:green,"95% Compliance")
EpiSim.plotquantiles(pop .- (Et80+St80),:purple,"80% Compliance")
plot!(1:tpday+1,y[1:tpday+1],lw=4, color=:red,label="growth phase")
plot!(tpday+1:ndays,y[tpday+1:ndays],color=:yellow,lw=4,label="plateau",xlim=(0, 120), ylim=(0,2*y[end]))

UndefVarError: UndefVarError: Mel not defined

## Enforce still stricter isolation

First set up the required network with isolated nodes (iso), then, simulate and plot everything.

In [7]:
iso=0.8 #was 0.95, I think 0.8 should be enough ... actually this parameter *may* significantly affect the results as it determines the susceptible pool size
pop=epiparam["pop"]
grd=Int(floor(sqrt(Int(floor(pop*(1-iso))))))
isosize=pop-grd^2
sg=SimpleGraph(isosize)
ws=watts_strogatz(grd^2, 4, 0.026)
isograph90=union(sg,ws)
Int(floor(sqrt(Int(floor(pop*(1-iso))))))

1148

In [8]:
St9,Et9,It9,Rt9=EpiSim.episim3(bamodel,wattstrog90, isograph90, epiparam, totItp, tpday+2, 1, 180, 400)

100.0%┣█████████████████████████████████████┫ 400/400 [03:29:05<00:00, 0.0 it/s]


(UInt64[0x000000000064a0f4 0x000000000064a0f4 … 0x000000000064a0f4 0x000000000064a0f4; 0x000000000064a0f4 0x000000000064a0f4 … 0x000000000064a0f4 0x000000000064a0f4; … ; 0x00000000006499b5 0x0000000000649b51 … 0x000000000064995b 0x00000000006497c4; 0x00000000006499b5 0x0000000000649b51 … 0x000000000064995b 0x00000000006497c4], UInt64[0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; 0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; … ; 0x0000000000000042 0x0000000000000033 … 0x0000000000000056 0x0000000000000078; 0x0000000000000042 0x0000000000000033 … 0x0000000000000056 0x0000000000000078], UInt64[0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; 0x0000000000000000 0x0000000000000000 … 0x0000000000000000 0x0000000000000000; … ; 0x0000000000000012 0x0000000000000018 … 0x000000000000001d 0x000000000000002a; 0x0000000000000012 0x0000000000000018 … 0x000000000000001d 0x000000000000002a], UInt64[0x000000

In [68]:
th=459 #number of active infecteds - this sets the day from which to make predicions
tp=count(x->x<th,y)
ddt(z,zt)=count(z->z>0, z[1:zt])+ count(z->z<0, z[zt+1:end])
~,tpday=findmax([ddt(diff(diff(y)),nx) for nx in 1:(ndays-2)])
#this is the turning point between exponential growth and decay. totItp total infections at day tpday
totItp=y[tpday+1]
plot(ddays[1:tpday+1],y[1:tpday+1],lw=4,label="growth phase",title="Perth, Western Australia",size=(1800,1200))
plot!(ddays[tpday+1:ndays],y[tpday+1:ndays],lw=4,seriescolor=:black,label="plateau")
(Sp,Ep,Ip,Rp) = EpiSim.epipred(th, St80,Et80,It80,Rt80)
lnp,~=size(Ip)
EpiSim.plotqnt((tp+1):tp+lnp,Ip+Rp,:red,"80% distancing 21/3")
(Sp,Ep,Ip,Rp) = EpiSim.epipred(th, St9,Et9,It9,Rt9)
lnp,~=size(Ip)
EpiSim.plotqnt((tp+1):tp+lnp,Ip+Rp,:green,"90% isolating 23/3")
plot!(ddays[tpday+1:ndays],y[tpday+1:ndays],lw=4,seriescolor=:black,label=false,xlimit=(0,150),ylimit=(0,3000))

<!DOCTYPE html>
 
 
 Plots.jl

In [70]:
using Statistics

In [100]:
plot()

<!DOCTYPE html>
 
 
 Plots.jl

In [102]:
EpiSim.plotquantiles(EE,:green)
EpiSim.plotquantiles(II,:red)

EpiSim.plotquantiles(RR,:black)



<!DOCTYPE html>
 
 
 Plots.jl

In [88]:
maximum(Int.(Ip))

661

In [103]:
RR = Rp[2:end,:] - Rp[1:end-1,:] ### daily increase of removed
II = RR+Ip[2:end,:]-Ip[1:(end-1),:] ### daily increase of infected
EE = II+Ep[2:end,:]-Ep[1:(end-1),:] ### daily increase of exposed
ET = Ep[2:end,:] ### current number of exposed

82×349 Array{UInt64,2}:
 0x0000000000000021  0x0000000000000041  …  0x0000000000000164
 0x0000000000000021  0x0000000000000044     0x0000000000000147
 0x000000000000001f  0x000000000000003d     0x0000000000000127
 0x000000000000001d  0x0000000000000037     0x000000000000010f
 0x000000000000001d  0x0000000000000039     0x0000000000000102
 0x000000000000001c  0x0000000000000032  …  0x00000000000000ee
 0x000000000000001c  0x0000000000000037     0x00000000000000d8
 0x000000000000001b  0x0000000000000035     0x00000000000000cc
 0x000000000000001a  0x0000000000000037     0x00000000000000bb
 0x0000000000000016  0x0000000000000035     0x00000000000000b4
 0x0000000000000018  0x000000000000002c  …  0x00000000000000a5
 0x0000000000000019  0x000000000000002e     0x000000000000009a
 0x000000000000001a  0x000000000000002a     0x0000000000000093
                  ⋮                      ⋱  
 0x0000000000000010  0x0000000000000013  …  0x000000000000001a
 0x0000000000000010  0x0000000000000013     0x000

In [115]:
plot(II,ET,seriestype=:scatter,legend=false,title="Hidden cases",xlabel="new infections", ylabel="total exposed",xlim=(0,100),ylim=(0, 600))

<!DOCTYPE html>
 
 
 Plots.jl

In [164]:
ninf=40
texp=300
hidden=zeros(Int64, texp+1, ninf+1)
(ndays,nsims)=size(II)
for i in 1:ndays
    for j in 1:nsims
        xi=II[i,j]
        xj=ET[i,j]
        if xi<ninf && xj<texp
            hidden[xj+1,xi+1] += 1
        end
    end
end
hidpdf=Array{Float64, 2}(undef, texp+1, ninf+1)
for i in 1:(ninf+1)
    hidpdf[:, i] = hidden[:, i] / sum(hidden[:, i])
end

In [186]:
heatmap(0:40,0:300, hidpdf, title="PDF of undetected infections", xlabel="number of new infected", ylabel="number of hidden exposed",ylim=(0,100), xlim=(0,20), color=cgrad([:white,:orange, :red], [0.1, 0.3, 0.8]) )

<!DOCTYPE html>
 
 
 Plots.jl

In [168]:
plot(hidpdf,seriestype=:surf, color=:OrRd)

<!DOCTYPE html>
 
 
 Plots.jl